# Loading recent Sentinel-2 data using STAC and Dask


In [1]:
import pystac_client
import odc.stac
from datetime import datetime, timedelta

import os
import dask
from dask.distributed import LocalCluster, Client

# Connect to the DEA Explorer STAC API to allow searching for data
stac_client = pystac_client.Client.open("https://explorer.dea.ga.gov.au/stac")

# To load data via STAC, we must configure appropriate access to data stored on
# DEA’s Amazon S3 buckets. This can be done with the odc.stac.configure_rio function.
# The configuration below must be used when loading any DEA data through the STAC API.
odc.stac.configure_rio(
    cloud_defaults=True,
    aws={"aws_unsigned": True},
)

# Launch Dask cluster
prefix = os.environ.get('JUPYTERHUB_SERVICE_PREFIX', '/')
dask.config.set({"distributed.dashboard.link": prefix + "proxy/{port}/status"})
cluster = LocalCluster(n_workers=2, threads_per_worker=1, memory_limit=0, processes=True)  
client = Client(cluster)
client

<Client: 'tcp://127.0.0.1:35019' processes=2 threads=2>

## Configure analysis

In [2]:
# Set spatial bounding box to load
bbox = [123, -10, 146, -20]

# Set number of days to look back through time
time_window = 2

# Bands to load
bands = ["nbart_swir_2", "nbart_swir_3"]   # ["nbart_red", "nbart_green", "nbart_blue"] 

## Search for data

In [3]:
# Calculate time query
end = datetime.now()
start = end - timedelta(days=time_window)
time = f"{start:%Y-%m-%d}/{end:%Y-%m-%d}"

# Search for STAC items
query = stac_client.search(
    collections=["ga_s2am_ard_3", "ga_s2bm_ard_3"],
    bbox=bbox,
    datetime=time,
)
items = list(query.items())
print(f"Items found: {len([i.properties['datetime'] for i in items])}")

Items found: 223


## Load data

In [4]:
# lazy load into xarray
ds = odc.stac.load(
    items,
    bbox=bbox,
    measurements=bands,
    crs="EPSG:3577",
    groupby="solar_day",
    resolution=100,
    chunks={"x": 2048, "y": 2048},
)
ds

<xarray.Dataset> Size: 5GB
Dimensions:       (y: 11401, x: 25892, time: 2)
Coordinates:
  * y             (y) float64 91kB -1.084e+06 -1.084e+06 ... -2.224e+06
  * x             (x) float64 207kB -1.014e+06 -1.014e+06 ... 1.575e+06
    spatial_ref   int32 4B 3577
  * time          (time) datetime64[ns] 16B 2024-08-27T01:09:53.664031 2024-0...
Data variables:
    nbart_swir_2  (time, y, x) float32 2GB dask.array<chunksize=(1, 2048, 2048), meta=np.ndarray>
    nbart_swir_3  (time, y, x) float32 2GB dask.array<chunksize=(1, 2048, 2048), meta=np.ndarray>

### Calculate median composite
All computation is done lazily for now

In [5]:
# Normalise between 0 and 1
ds = ds * 0.0001

# Calculate index (please verify, may not be correct!)
mirbi = 10.0 * ds.nbart_swir_2 - 9.8 * ds.nbart_swir_2 + 2.0

# Calculate median
mirbi_median = mirbi.median(dim="time")

# Start computation
mirbi_median = mirbi_median.compute()

/env/lib/python3.10/site-packages/dask/utils.py:78: RuntimeWarning: All-NaN slice encountered
  return func(*args, **kwargs)
/env/lib/python3.10/site-packages/dask/utils.py:78: RuntimeWarning: All-NaN slice encountered
  return func(*args, **kwargs)
/env/lib/python3.10/site-packages/dask/utils.py:78: RuntimeWarning: All-NaN slice encountered
  return func(*args, **kwargs)
/env/lib/python3.10/site-packages/dask/utils.py:78: RuntimeWarning: All-NaN slice encountered
  return func(*args, **kwargs)
/env/lib/python3.10/site-packages/dask/utils.py:78: RuntimeWarning: All-NaN slice encountered
  return func(*args, **kwargs)
/env/lib/python3.10/site-packages/dask/utils.py:78: RuntimeWarning: All-NaN slice encountered
  return func(*args, **kwargs)
/env/lib/python3.10/site-packages/dask/utils.py:78: RuntimeWarning: All-NaN slice encountered
  return func(*args, **kwargs)
/env/lib/python3.10/site-packages/dask/utils.py:78: RuntimeWarning: All-NaN slice encountered
  return func(*args, **kwargs)


## Export to file

In [6]:
# Export to COG
mirbi_median.odc.write_cog("mirbi_median_cog.tif", overwrite=True)

PosixPath('mirbi_median_cog.tif')

In [7]:
mirbi_median.odc.explore()